In [44]:

import os

import numpy as np
import pandas as pd

import torch
from torch.utils.data import Dataset, DataLoader
from torchvision import datasets
from torchvision.transforms import ToTensor
import matplotlib.pyplot as plt

import cv2

import torch.nn as nn

from tensorflow.keras.layers import Dense, SimpleRNN, Input, Embedding
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import Tokenizer, text_to_word_sequence
from tensorflow.keras.utils import to_categorical

In [2]:
data = pd.read_csv("train/train.csv")

In [3]:
texts = data["description"].to_list()

In [4]:
texts

['С вами Макс Климток и это шоу Правильная цена! Шоу, в котором участники зарабатывают баллы, угадывая правильные цены товаров и услуг. Сегодня мы узнаем, как в ценах ориентируются Бинет Сен,  Женя Лизогубенко и Кика Кика За просмотр шоу вы также можете заплатить свою цену - поставить лайк, подписаться на канал и оставить комментарий.',
 'В этом новом выпуске нас ждут не менее новые и безумные челленжи наших сумасшедших и харизматичных ведущих! Аварии, гонка, надувные женщины... Что ждет их на очередном пути к победе. Ставь лайки, пиши комментарии и подписывайся. Агабекян Авет ... Саша Стоун / Макс Игумнов /   #челленджи #челленджи2021',
 'Привет, это Султан и Авет! Мы опять хаваем вкусное и не очень вкусное, а также обсуждаем всевозможные зашквары. В этом выпуске мы высмеяли дешевый пресс Давы, поржали над тиктоками Погребняк, Обсудили Тбилиси и конечно же не смогли пройти мимо скандала со ВкусВиллом. Ставьте лайки и комменты, приятного просмотра. #шоу #хашлама #дава  Авет - Султан - 

In [78]:
itog_desc = []

for i in texts:
    for j in range(20):
        itog_desc.append(i)

In [6]:
len(itog_desc)

10000

In [79]:
itog_desc[0]

'С вами Макс Климток и это шоу Правильная цена! Шоу, в котором участники зарабатывают баллы, угадывая правильные цены товаров и услуг. Сегодня мы узнаем, как в ценах ориентируются Бинет Сен,  Женя Лизогубенко и Кика Кика За просмотр шоу вы также можете заплатить свою цену - поставить лайк, подписаться на канал и оставить комментарий.'

In [80]:
mas = itog_desc

In [81]:
print(mas[0])

С вами Макс Климток и это шоу Правильная цена! Шоу, в котором участники зарабатывают баллы, угадывая правильные цены товаров и услуг. Сегодня мы узнаем, как в ценах ориентируются Бинет Сен,  Женя Лизогубенко и Кика Кика За просмотр шоу вы также можете заплатить свою цену - поставить лайк, подписаться на канал и оставить комментарий.


In [82]:
with open("stop-words-russian.txt", "r") as sw:
    stop_words = sw.read().split()[1:]
    
    itog = []
    for i in range(len(mas)):
        mas[i] = mas[i].split()
        arr = []
        for j in range(len(mas[i])):
            if mas[i][j] not in stop_words:
                arr.append(mas[i][j])
        itog.append(" ".join(arr))


In [123]:
itog

['С Макс Климток шоу Правильная цена! Шоу, котором участники зарабатывают баллы, угадывая правильные цены товаров услуг. Сегодня узнаем, ценах ориентируются Бинет Сен, Женя Лизогубенко Кика Кика За просмотр шоу можете заплатить цену - поставить лайк, подписаться канал оставить комментарий.',
 'С Макс Климток шоу Правильная цена! Шоу, котором участники зарабатывают баллы, угадывая правильные цены товаров услуг. Сегодня узнаем, ценах ориентируются Бинет Сен, Женя Лизогубенко Кика Кика За просмотр шоу можете заплатить цену - поставить лайк, подписаться канал оставить комментарий.',
 'С Макс Климток шоу Правильная цена! Шоу, котором участники зарабатывают баллы, угадывая правильные цены товаров услуг. Сегодня узнаем, ценах ориентируются Бинет Сен, Женя Лизогубенко Кика Кика За просмотр шоу можете заплатить цену - поставить лайк, подписаться канал оставить комментарий.',
 'С Макс Климток шоу Правильная цена! Шоу, котором участники зарабатывают баллы, угадывая правильные цены товаров услуг. 

In [124]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /Users/vlyrdv/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [128]:
def tokenize_texts(texts):
    tokenized_texts = []
    for text in texts:
        tokens = nltk.word_tokenize(text.lower())
        tokenized_texts.append(tokens)
    return tokenized_texts

In [139]:
texts = itog
tokenized_texts = tokenize_texts(texts)
print(tokenized_texts)

[['с', 'макс', 'климток', 'шоу', 'правильная', 'цена', '!', 'шоу', ',', 'котором', 'участники', 'зарабатывают', 'баллы', ',', 'угадывая', 'правильные', 'цены', 'товаров', 'услуг', '.', 'сегодня', 'узнаем', ',', 'ценах', 'ориентируются', 'бинет', 'сен', ',', 'женя', 'лизогубенко', 'кика', 'кика', 'за', 'просмотр', 'шоу', 'можете', 'заплатить', 'цену', '-', 'поставить', 'лайк', ',', 'подписаться', 'канал', 'оставить', 'комментарий', '.'], ['с', 'макс', 'климток', 'шоу', 'правильная', 'цена', '!', 'шоу', ',', 'котором', 'участники', 'зарабатывают', 'баллы', ',', 'угадывая', 'правильные', 'цены', 'товаров', 'услуг', '.', 'сегодня', 'узнаем', ',', 'ценах', 'ориентируются', 'бинет', 'сен', ',', 'женя', 'лизогубенко', 'кика', 'кика', 'за', 'просмотр', 'шоу', 'можете', 'заплатить', 'цену', '-', 'поставить', 'лайк', ',', 'подписаться', 'канал', 'оставить', 'комментарий', '.'], ['с', 'макс', 'климток', 'шоу', 'правильная', 'цена', '!', 'шоу', ',', 'котором', 'участники', 'зарабатывают', 'баллы',

In [140]:
id_num = []
for i in tokenized_texts:
    for j in i:
        id_num.append(j)

In [141]:
id_num = list(set(id_num))

In [142]:
id_num

['расслабится',
 'достопримечательностью',
 'пряник',
 'дети',
 'алиса',
 'придумают',
 'карина',
 'краснова',
 'вован',
 'коаст',
 'устроились',
 'костромы',
 '2021',
 'получилось',
 'городароссии',
 'зале',
 'афоня',
 'рождественском',
 'контракт',
 'компании',
 'приглашённым',
 'новостях',
 'слона',
 'игнатьев',
 'курицей',
 'принимается',
 'встречают',
 'применить',
 'массовой',
 'истомин',
 'прямая',
 'смерти',
 'ведь',
 'омарвбольшомгороде',
 'поклонникам',
 'попытки',
 'получает',
 'персидского',
 'планете',
 'холодный',
 'нарубить',
 'джарахича',
 'мальчику',
 'кандидатам',
 'новогодних',
 '24:55',
 'ксения',
 'починить',
 'депутатом',
 'обычным',
 '9',
 'тенденция',
 'остались',
 'берутся',
 'тяпу',
 'ставка',
 'начальника',
 'казармам',
 'настоящая',
 'задумка',
 'сытно',
 'дубровский',
 'потрясающем',
 'популярные',
 'оганисян',
 'пропал',
 'страна',
 'бытом',
 'переобуть',
 'соболева',
 'прошёл',
 'скрывают',
 'следственный',
 'нарисованное',
 'провисела',
 'маврин',
 'прие

In [143]:
for i in range(len(tokenized_texts)):
    for j in range(len(tokenized_texts[i])):
        tokenized_texts[i][j] = id_num.index(tokenized_texts[i][j])

In [145]:
len(tokenized_texts)

10000